In [ ]:
%pip install setuptools

In [4]:
import pandas as pd
import numpy as np
import os.path
import os
import nltk
import string
# import textstat
# from textstat import Readability
from functools import reduce
from nltk.util import ngrams
from collections import Counter
from nltk.tokenize import sent_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.corpus import words as nltk_words
nltk.download('words')
nltk.download('punkt')

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\user\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\user\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [5]:
deepfake_text = pd.read_csv('data/deepfake-text-detect/train.csv')

In [6]:
human_text = deepfake_text[deepfake_text['label'] == 1][0:10000]
chatgpt_text = deepfake_text[deepfake_text['label'] == 0][0:10000]

In [7]:
def csv_to_text_files(dataframe, output_folder, start_index=1):
    os.makedirs(output_folder, exist_ok=True)
    essays = dataframe['text']
    id_number = start_index - 1 
    for essay in essays:
        id_number += 1
        file_path = os.path.join(output_folder, f'{id_number}.txt')
        with open(file_path, 'w', encoding='utf-8') as file:
            file.write(essay)


In [8]:
folder_paths = [
        ('data/deepfake-text-detect/human', 1),
        ('data/deepfake-text-detect/chatgpt', 0)
    ]

In [9]:
csv_to_text_files(chatgpt_text, 'data/deepfake-text-detect/chatgpt')
chatgpt_path = 'data/deepfake-text-detect/chatgpt'
max_index = max([int(filename.split('.')[0]) for filename in os.listdir(chatgpt_path)]) if os.listdir(chatgpt_path) else 0



In [10]:
csv_to_text_files(human_text, 'data/deepfake-text-detect/human', start_index=max_index + 1)

## Feautre Extraction

In [70]:
def dataset_looper(extracted_feature_list, feature_extraction_func):
    base_dir = os.getcwd()  # Base directory
    file_count = 0  # Keep track of the total number of processed files
    
    for folder_path, _ in folder_paths:  # Ignore the label
        full_path = os.path.join(base_dir, folder_path)
        
        if not os.path.exists(full_path):
            print(f"Directory does not exist: {full_path}")
            continue
        
        local_files = sorted(os.listdir(full_path), key=lambda x: int(x.split('.')[0]))
        for file in local_files:
            if file.endswith(".txt"):
                file_path = os.path.join(full_path, file)
                file_count += 1  # Increment file_count for each file processed
                extracted_features = feature_extraction_func(file_path)
                extracted_feature_list.append((file_count, extracted_features))  # No label included


In [71]:
essays_labels = []
base_dir = os.getcwd()

file_count = 0  # Maintain a count across both directories

for folder_path, _ in folder_paths:  # Ignore the label here as well
    full_path = os.path.join(base_dir, folder_path)
    
    if not os.path.exists(full_path):
        print(f"Directory does not exist: {full_path}")
        continue

    local_files = sorted(os.listdir(full_path), key=lambda x: int(x.split('.')[0]))
    for file in local_files:
        if file.endswith(".txt"):
            file_count += 1  # Increment file_count for each file processed
            essays_labels.append({'Id': file_count})  # Only ID is recorded


In [72]:
# Sort essay labels
essays_labels = sorted(essays_labels, key=lambda x: x['Id'])
essays_labels

[{'Id': 1},
 {'Id': 2},
 {'Id': 3},
 {'Id': 4},
 {'Id': 5},
 {'Id': 6},
 {'Id': 7},
 {'Id': 8},
 {'Id': 9},
 {'Id': 10},
 {'Id': 11},
 {'Id': 12},
 {'Id': 13},
 {'Id': 14},
 {'Id': 15},
 {'Id': 16},
 {'Id': 17},
 {'Id': 18},
 {'Id': 19},
 {'Id': 20},
 {'Id': 21},
 {'Id': 22},
 {'Id': 23},
 {'Id': 24},
 {'Id': 25},
 {'Id': 26},
 {'Id': 27},
 {'Id': 28},
 {'Id': 29},
 {'Id': 30},
 {'Id': 31},
 {'Id': 32},
 {'Id': 33},
 {'Id': 34},
 {'Id': 35},
 {'Id': 36},
 {'Id': 37},
 {'Id': 38},
 {'Id': 39},
 {'Id': 40},
 {'Id': 41},
 {'Id': 42},
 {'Id': 43},
 {'Id': 44},
 {'Id': 45},
 {'Id': 46},
 {'Id': 47},
 {'Id': 48},
 {'Id': 49},
 {'Id': 50},
 {'Id': 51},
 {'Id': 52},
 {'Id': 53},
 {'Id': 54},
 {'Id': 55},
 {'Id': 56},
 {'Id': 57},
 {'Id': 58},
 {'Id': 59},
 {'Id': 60},
 {'Id': 61},
 {'Id': 62},
 {'Id': 63},
 {'Id': 64},
 {'Id': 65},
 {'Id': 66},
 {'Id': 67},
 {'Id': 68},
 {'Id': 69},
 {'Id': 70},
 {'Id': 71},
 {'Id': 72},
 {'Id': 73},
 {'Id': 74},
 {'Id': 75},
 {'Id': 76},
 {'Id': 77},
 {'Id': 

### Lexical Features (120)

#### Total # of characters (1)

In [73]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks
essay_total_char_counts = []

# how do we add the dataframes together, we combine them based on a certain ID. how would we do that consitently? 
# name a column that specifically has that essay's name?

def total_char_in_essay(file_path): 
    charCount = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
        charCount+=len(data)
    return charCount

dataset_looper(essay_total_char_counts, total_char_in_essay)

In [74]:
essay_total_char_counts

[(1, 1238),
 (2, 1364),
 (3, 1628),
 (4, 2269),
 (5, 1240),
 (6, 1901),
 (7, 5656),
 (8, 1654),
 (9, 4907),
 (10, 2275),
 (11, 4333),
 (12, 3480),
 (13, 605),
 (14, 1746),
 (15, 1661),
 (16, 3021),
 (17, 1493),
 (18, 1909),
 (19, 4366),
 (20, 2175),
 (21, 960),
 (22, 3848),
 (23, 1461),
 (24, 2876),
 (25, 549),
 (26, 2269),
 (27, 1331),
 (28, 879),
 (29, 615),
 (30, 2959),
 (31, 3056),
 (32, 3220),
 (33, 2675),
 (34, 758),
 (35, 585),
 (36, 1617),
 (37, 2246),
 (38, 2644),
 (39, 3752),
 (40, 1498),
 (41, 3386),
 (42, 3086),
 (43, 2493),
 (44, 2416),
 (45, 3428),
 (46, 6277),
 (47, 2386),
 (48, 1801),
 (49, 1179),
 (50, 2521),
 (51, 2720),
 (52, 1324),
 (53, 4460),
 (54, 890),
 (55, 567),
 (56, 1035),
 (57, 1306),
 (58, 809),
 (59, 2624),
 (60, 1461),
 (61, 1872),
 (62, 1558),
 (63, 2063),
 (64, 1346),
 (65, 1891),
 (66, 2160),
 (67, 4975),
 (68, 2764),
 (69, 1063),
 (70, 1800),
 (71, 1861),
 (72, 2858),
 (73, 2700),
 (74, 2701),
 (75, 2340),
 (76, 1768),
 (77, 2089),
 (78, 2508),
 (79,

#### Percentage of digits (1)

In [75]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks
essays_digit_percentage = []

# how do we add the dataframes together, we combine them based on a certain ID. how would we do that consitently? 
# name a column that specifically has that essay's name?

def total_char_in_essay(file_path): 
    digit_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    for char in data:
        if char.isdigit():
            digit_count+=1
    total_essay_char = len(data)
    essay_digit_percentage = digit_count/total_essay_char
    return essay_digit_percentage

dataset_looper(essays_digit_percentage, total_char_in_essay)

In [76]:
essays_digit_percentage

[(1, 0.0),
 (2, 0.002932551319648094),
 (3, 0.0012285012285012285),
 (4, 0.0022036139268400176),
 (5, 0.0),
 (6, 0.0021041557075223566),
 (7, 0.0003536067892503536),
 (8, 0.0),
 (9, 0.0),
 (10, 0.00043956043956043956),
 (11, 0.00046157396722824835),
 (12, 0.00603448275862069),
 (13, 0.0),
 (14, 0.0),
 (15, 0.0),
 (16, 0.0019860973187686196),
 (17, 0.0),
 (18, 0.0),
 (19, 0.0),
 (20, 0.0),
 (21, 0.0),
 (22, 0.0010395010395010396),
 (23, 0.0),
 (24, 0.0027816411682892906),
 (25, 0.0),
 (26, 0.0022036139268400176),
 (27, 0.002253944402704733),
 (28, 0.0),
 (29, 0.0),
 (30, 0.0),
 (31, 0.0022905759162303663),
 (32, 0.0),
 (33, 0.0011214953271028037),
 (34, 0.005277044854881266),
 (35, 0.003418803418803419),
 (36, 0.0),
 (37, 0.0),
 (38, 0.0011346444780635401),
 (39, 0.0005330490405117271),
 (40, 0.0),
 (41, 0.0017720023626698169),
 (42, 0.004536616979909268),
 (43, 0.0),
 (44, 0.0037251655629139072),
 (45, 0.0005834305717619603),
 (46, 0.005416600286761192),
 (47, 0.0),
 (48, 0.0),
 (49, 0

#### Percentage of letters (1)

In [77]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks
essays_letter_percentage = []

# how do we add the dataframes together, we combine them based on a certain ID. how would we do that consitently? 
# name a column that specifically has that essay's name?

def total_letter_percentage(file_path): 
    letter_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    for char in data:
        if char.isalpha():
            letter_count+=1
    total_essay_char = len(data)
    essay_letter_percentage = letter_count/total_essay_char
    return essay_letter_percentage

dataset_looper(essays_letter_percentage, total_letter_percentage)


In [78]:
essays_letter_percentage

[(1, 0.7859450726978998),
 (2, 0.7741935483870968),
 (3, 0.777027027027027),
 (4, 0.7800793301013662),
 (5, 0.8104838709677419),
 (6, 0.7916885849552867),
 (7, 0.7956152758132956),
 (8, 0.786577992744861),
 (9, 0.8013042592215203),
 (10, 0.7960439560439561),
 (11, 0.7985229633048696),
 (12, 0.7847701149425287),
 (13, 0.7966942148760331),
 (14, 0.8035509736540665),
 (15, 0.7959060806742926),
 (16, 0.7772260840781199),
 (17, 0.7916945746818487),
 (18, 0.7941330539549503),
 (19, 0.7963811268896015),
 (20, 0.7816091954022989),
 (21, 0.8041666666666667),
 (22, 0.7897609147609148),
 (23, 0.7919233401779603),
 (24, 0.7990264255910987),
 (25, 0.8178506375227687),
 (26, 0.8012340237990304),
 (27, 0.7821187077385424),
 (28, 0.7838452787258248),
 (29, 0.7934959349593496),
 (30, 0.7928354173707334),
 (31, 0.7768324607329843),
 (32, 0.808695652173913),
 (33, 0.7992523364485982),
 (34, 0.7862796833773087),
 (35, 0.788034188034188),
 (36, 0.8058132343846629),
 (37, 0.7849510240427426),
 (38, 0.799924

#### Percentage of uppercase letters (1)

In [79]:
uppercase_percentage = []

def total_uppercase_percentage(file_path): 
    uppercase_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()
    for char in data:
        if char.isupper():
            uppercase_count+=1
    total_essay_char = len(data)
    essay_uppercase_percentage = uppercase_count/total_essay_char
    return essay_uppercase_percentage

dataset_looper(uppercase_percentage, total_uppercase_percentage)

In [80]:
uppercase_percentage

[(1, 0.03150242326332795),
 (2, 0.028592375366568914),
 (3, 0.048525798525798525),
 (4, 0.02379903040987219),
 (5, 0.01129032258064516),
 (6, 0.02524986849026828),
 (7, 0.01608910891089109),
 (8, 0.02357920193470375),
 (9, 0.024454860403505196),
 (10, 0.026813186813186812),
 (11, 0.02284791137779829),
 (12, 0.031609195402298854),
 (13, 0.011570247933884297),
 (14, 0.01718213058419244),
 (15, 0.024081878386514148),
 (16, 0.026481297583581597),
 (17, 0.01942397856664434),
 (18, 0.021477213200628602),
 (19, 0.013284470911589555),
 (20, 0.02620689655172414),
 (21, 0.015625),
 (22, 0.018970893970893972),
 (23, 0.03148528405201916),
 (24, 0.025382475660639777),
 (25, 0.03278688524590164),
 (26, 0.011458792419568091),
 (27, 0.02404207362885049),
 (28, 0.01820250284414107),
 (29, 0.02113821138211382),
 (30, 0.020615072659682324),
 (31, 0.028795811518324606),
 (32, 0.031055900621118012),
 (33, 0.018691588785046728),
 (34, 0.011873350923482849),
 (35, 0.015384615384615385),
 (36, 0.0179344465058

#### Frequency of character unigram (36)

tokenization, lowercasing, stemming, and stop word removal

v1 lowercase and removal of punctuations and regex

In [81]:
char_frequency = {
    'a': 0, 
    'b': 0, 
    'c': 0, 
    'd': 0, 
    'e': 0, 
    'f': 0, 
    'g': 0, 
    'h': 0, 
    'i': 0, 
    'j': 0, 
    'k': 0, 
    'l': 0, 
    'm': 0, 
    'n': 0, 
    'o': 0, 
    'p': 0, 
    'q': 0, 
    'r': 0, 
    's': 0, 
    't': 0, 
    'u': 0, 
    'v': 0, 
    'w': 0, 
    'x': 0, 
    'y': 0, 
    'z': 0, 
}

essays_char_frequency = []
def check_char_frequency(file_path):
    char_frequency_copy = char_frequency.copy() 
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    for char in data:
        for x in char_frequency_copy:
            if char == x:
                char_frequency_copy[x] +=1
              
    renamed_char_frequency_copy = {}
    for char, values in char_frequency_copy.items():
        renamed_char_frequency_copy[f'Char frequency - {char}'] = values
    
    return renamed_char_frequency_copy
dataset_looper(essays_char_frequency, check_char_frequency)
# essays_char_frequency
new_char_freq_array = []
for item in essays_char_frequency:
    Id = 0
    char_freq_dict = 1
    item[char_freq_dict]['Id'] = item[Id] 
    new_char_freq_array.append(item[char_freq_dict])
    
essays_char_frequency = new_char_freq_array

In [82]:
essays_char_frequency

[{'Char frequency - a': 86,
  'Char frequency - b': 13,
  'Char frequency - c': 34,
  'Char frequency - d': 22,
  'Char frequency - e': 119,
  'Char frequency - f': 26,
  'Char frequency - g': 27,
  'Char frequency - h': 46,
  'Char frequency - i': 78,
  'Char frequency - j': 1,
  'Char frequency - k': 9,
  'Char frequency - l': 37,
  'Char frequency - m': 30,
  'Char frequency - n': 69,
  'Char frequency - o': 71,
  'Char frequency - p': 17,
  'Char frequency - q': 1,
  'Char frequency - r': 52,
  'Char frequency - s': 66,
  'Char frequency - t': 78,
  'Char frequency - u': 32,
  'Char frequency - v': 16,
  'Char frequency - w': 18,
  'Char frequency - x': 0,
  'Char frequency - y': 24,
  'Char frequency - z': 1,
  'Id': 1},
 {'Char frequency - a': 94,
  'Char frequency - b': 16,
  'Char frequency - c': 24,
  'Char frequency - d': 37,
  'Char frequency - e': 127,
  'Char frequency - f': 31,
  'Char frequency - g': 26,
  'Char frequency - h': 42,
  'Char frequency - i': 77,
  'Char fre

#### Most common char bigrams (40)

In [83]:
essays_char_bigrams = []

def check_char_bigrams(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    most_common_forty_char_bigrams = Counter(list(ngrams(list(data), 2))).most_common(40)
    index = 1
    most_common_char_bigrams = {}
    for bigram in most_common_forty_char_bigrams:
        most_common_char_bigrams[f'Common char bigram {index}'] = bigram[1]
        index+=1
    return most_common_char_bigrams

dataset_looper(essays_char_bigrams, check_char_bigrams)

new_char_bigram_freq_list = []
for item in essays_char_bigrams:
    item[1]['Id'] = item[0] 
    new_char_bigram_freq_list.append(item[1])
    
essays_char_bigrams = new_char_bigram_freq_list

essays_char_bigrams

[{'Common char bigram 1': 42,
  'Common char bigram 2': 33,
  'Common char bigram 3': 22,
  'Common char bigram 4': 20,
  'Common char bigram 5': 19,
  'Common char bigram 6': 18,
  'Common char bigram 7': 17,
  'Common char bigram 8': 17,
  'Common char bigram 9': 16,
  'Common char bigram 10': 16,
  'Common char bigram 11': 16,
  'Common char bigram 12': 15,
  'Common char bigram 13': 14,
  'Common char bigram 14': 14,
  'Common char bigram 15': 14,
  'Common char bigram 16': 13,
  'Common char bigram 17': 13,
  'Common char bigram 18': 13,
  'Common char bigram 19': 13,
  'Common char bigram 20': 13,
  'Common char bigram 21': 12,
  'Common char bigram 22': 12,
  'Common char bigram 23': 12,
  'Common char bigram 24': 12,
  'Common char bigram 25': 12,
  'Common char bigram 26': 11,
  'Common char bigram 27': 11,
  'Common char bigram 28': 11,
  'Common char bigram 29': 11,
  'Common char bigram 30': 10,
  'Common char bigram 31': 10,
  'Common char bigram 32': 10,
  'Common char bi

#### Most common char trigrams (40)

In [84]:
essays_char_trigrams = []

def check_char_trigrams(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    most_common_forty_char_trigrams = Counter(list(ngrams(list(data), 3))).most_common(40)
    index = 1
    most_common_char_trigrams = {}
    for trigram in most_common_forty_char_trigrams:
        most_common_char_trigrams[f'Common char trigram {index}'] = trigram[1]
        index+=1
    return most_common_char_trigrams

dataset_looper(essays_char_trigrams, check_char_trigrams)

new_char_trigrams_freq_list = []
for item in essays_char_trigrams:
    item[1]['Id'] = item[0] 
    new_char_trigrams_freq_list.append(item[1])
    
essays_char_trigrams = new_char_trigrams_freq_list

essays_char_trigrams

[{'Common char trigram 1': 14,
  'Common char trigram 2': 10,
  'Common char trigram 3': 10,
  'Common char trigram 4': 9,
  'Common char trigram 5': 9,
  'Common char trigram 6': 8,
  'Common char trigram 7': 8,
  'Common char trigram 8': 8,
  'Common char trigram 9': 8,
  'Common char trigram 10': 7,
  'Common char trigram 11': 7,
  'Common char trigram 12': 7,
  'Common char trigram 13': 7,
  'Common char trigram 14': 7,
  'Common char trigram 15': 6,
  'Common char trigram 16': 6,
  'Common char trigram 17': 6,
  'Common char trigram 18': 6,
  'Common char trigram 19': 6,
  'Common char trigram 20': 6,
  'Common char trigram 21': 5,
  'Common char trigram 22': 5,
  'Common char trigram 23': 5,
  'Common char trigram 24': 5,
  'Common char trigram 25': 5,
  'Common char trigram 26': 5,
  'Common char trigram 27': 5,
  'Common char trigram 28': 5,
  'Common char trigram 29': 5,
  'Common char trigram 30': 5,
  'Common char trigram 31': 5,
  'Common char trigram 32': 5,
  'Common char

In [85]:
test = pd.DataFrame(essays_char_trigrams)
test

Common char trigram 1  Common char trigram 2  Common char trigram 3  \
0                         14                     10                     10   
1                         15                     13                     13   
2                         38                     27                     14   
3                         29                     21                     20   
4                         31                     25                     17   
...                      ...                    ...                    ...   
19995                     21                     15                     12   
19996                     23                     17                     10   
19997                     25                     19                     14   
19998                      9                      5                      5   
19999                     14                      8                      7   

       Common char trigram 4  Common char trigram 5  Common char trigram 6  \
0                          9                      9                      8   
1                         11                     10                     10   
2                         14                     13                     13   
3                         19                     18                     17   
4                         16                     14                      9   
...                      ...                    ...                    ...   
19995                     11                     11                     11   
19996                     10                      9                      8   
19997                     13                     12                     11   
19998                      5                      4                      4   
19999                      6                      5                      5   

       Common char trigram 7  Common char trigram 8  Common char trigram 9  \
0                          8                      8                      8   
1                         10                      9                      8   
2                         12                     11                     11   
3                         16                     15                     15   
4                          9                      9                      8   
...                      ...                    ...                    ...   
19995                     10                     10                     10   
19996                      7                      7                      7   
19997                     11                     11                     11   
19998                      4                      4                      4   
19999                      5                      4                      4   

       Common char trigram 10  ...  Common char trigram 32  \
0                           7  ...                     5.0   
1                           8  ...                     5.0   
2                          11  ...                     7.0   
3                          14  ...                     8.0   
4                           8  ...                     6.0   
...                       ...  ...                     ...   
19995                       9  ...                     5.0   
19996                       6  ...                     4.0   
19997                      10  ...                     6.0   
19998                       4  ...                     2.0   
19999                       4  ...                     3.0   

       Common char trigram 33  Common char trigram 34  Common char trigram 35  \
0                         4.0                     4.0                     4.0   
1                         5.0                     5.0                     5.0   
2                         7.0                     7.0                     7.0   
3                         8.0                     8.0                     8.0   
4                         5.0                 

### Lexical Features - Digits, special characters, punctuation chars (40)

#### Frequency of digits from 0 to 9 (10)

In [86]:
digit_frequency = {
    '0': 0,
    '1': 0, 
    '2': 0, 
    '3': 0, 
    '4': 0, 
    '5': 0, 
    '6': 0, 
    '7': 0, 
    '8': 0, 
    '9': 0, 
}

essays_digit_frequency = []
def check_digit_frequency(file_path):
    digit_frequency_copy = digit_frequency.copy() 
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    for char in data:
        for x in digit_frequency_copy:
            if char == x:
                digit_frequency_copy[x] +=1
    
    renamed_digit_frequency_copy = {}
    for digit, values in digit_frequency_copy.items():
        renamed_digit_frequency_copy[f'Digit frequency - {digit}'] = values
    return renamed_digit_frequency_copy

dataset_looper(essays_digit_frequency, check_digit_frequency)

new_digit_freq_array = []
for item in essays_digit_frequency:
    Id = 0
    digit_freq_dict = 1
    item[digit_freq_dict]['Id'] = item[Id] 
    new_digit_freq_array.append(item[digit_freq_dict])
    
essays_digit_frequency = new_digit_freq_array

In [87]:
essays_digit_frequency

[{'Digit frequency - 0': 0,
  'Digit frequency - 1': 0,
  'Digit frequency - 2': 0,
  'Digit frequency - 3': 0,
  'Digit frequency - 4': 0,
  'Digit frequency - 5': 0,
  'Digit frequency - 6': 0,
  'Digit frequency - 7': 0,
  'Digit frequency - 8': 0,
  'Digit frequency - 9': 0,
  'Id': 1},
 {'Digit frequency - 0': 0,
  'Digit frequency - 1': 0,
  'Digit frequency - 2': 1,
  'Digit frequency - 3': 1,
  'Digit frequency - 4': 1,
  'Digit frequency - 5': 1,
  'Digit frequency - 6': 0,
  'Digit frequency - 7': 0,
  'Digit frequency - 8': 0,
  'Digit frequency - 9': 0,
  'Id': 2},
 {'Digit frequency - 0': 0,
  'Digit frequency - 1': 1,
  'Digit frequency - 2': 0,
  'Digit frequency - 3': 0,
  'Digit frequency - 4': 0,
  'Digit frequency - 5': 0,
  'Digit frequency - 6': 0,
  'Digit frequency - 7': 0,
  'Digit frequency - 8': 1,
  'Digit frequency - 9': 0,
  'Id': 3},
 {'Digit frequency - 0': 2,
  'Digit frequency - 1': 2,
  'Digit frequency - 2': 0,
  'Digit frequency - 3': 0,
  'Digit fre

#### Special Characters e.g &, %, etc. (30)

In [88]:
special_char_frequency = {
    '~': 0, 
    '`': 0, 
    '!': 0, 
    '@': 0, 
    '#': 0, 
    '$': 0, 
    '%': 0, 
    '^': 0, 
    '&': 0, 
    '*': 0, 
    '(': 0, 
    ')': 0, 
    '-': 0, 
    '_': 0, 
    '+': 0, 
    '=': 0, 
    '{': 0, 
    '}': 0, 
    '[': 0, 
    ']': 0, 
    '|': 0, 
    '\\': 0, 
    ':': 0, 
    ';': 0, 
    '"': 0, 
    '\'': 0, 
    '<': 0,
    ',': 0, 
    '>': 0, 
    '.': 0, 
    '?': 0, 
    '/': 0, 
}

essays_special_char_frequency = []
def check_special_char_frequency(file_path):
    special_char_frequency_copy = special_char_frequency.copy() 
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    for char in data:
        for x in special_char_frequency_copy:
            if char == x:
                special_char_frequency_copy[x] +=1
        if char == '”' or char == '“':
            special_char_frequency_copy['"'] +=1
        elif char == '‘' or char == '’':
            special_char_frequency_copy["'"] +=1
        elif char == '—':
            special_char_frequency_copy['-'] +=1
    
    renamed_special_char_frequency_copy = {}
    for char, values in special_char_frequency_copy.items():
        renamed_special_char_frequency_copy[f'Special char frequency - {char}'] = values
    
    return renamed_special_char_frequency_copy

dataset_looper(essays_special_char_frequency, check_special_char_frequency)

new_special_char_frequency = []
for item in essays_special_char_frequency:
    item[1]['Id'] = item[0] 
    new_special_char_frequency.append(item[1])
    
essays_special_char_frequency = new_special_char_frequency

In [89]:
essays_special_char_frequency

[{'Special char frequency - ~': 0,
  'Special char frequency - `': 0,
  'Special char frequency - !': 3,
  'Special char frequency - @': 0,
  'Special char frequency - #': 0,
  'Special char frequency - $': 0,
  'Special char frequency - %': 0,
  'Special char frequency - ^': 0,
  'Special char frequency - &': 0,
  'Special char frequency - *': 0,
  'Special char frequency - (': 0,
  'Special char frequency - )': 0,
  'Special char frequency - -': 1,
  'Special char frequency - _': 0,
  'Special char frequency - +': 0,
  'Special char frequency - =': 0,
  'Special char frequency - {': 0,
  'Special char frequency - }': 0,
  'Special char frequency - [': 4,
  'Special char frequency - ]': 4,
  'Special char frequency - |': 0,
  'Special char frequency - \\': 0,
  'Special char frequency - :': 1,
  'Special char frequency - ;': 0,
  'Special char frequency - "': 0,
  "Special char frequency - '": 6,
  'Special char frequency - <': 0,
  'Special char frequency - ,': 10,
  'Special char fr

In [90]:
pd.set_option('display.max_columns', None)
special_char_df = pd.DataFrame(essays_special_char_frequency)
special_char_df.describe()
# print(np.sum(special_char_df[["'"]]))
# print(np.sum(special_char_df[['"']]))
# print(np.sum(special_char_df[["-"]]))
# '    398
# dtype: int64
# "    131
# dtype: int64
# -    366
# dtype: int64

# “    6.0
# dtype: float64
# ”    7.0
# dtype: float64
# ‘    4.0
# dtype: float64
# ’    115.0
# dtype: float64
# —    3.0
# dtype: float64
# print(np.sum(special_char_df[["'"]]))
# values_not_detected = [~, `, @, #, $, ^, *, _, =, {, }, |, <, >] = 14 values

Special char frequency - ~  Special char frequency - `  \
count                     20000.0                     20000.0   
mean                          0.0                         0.0   
std                           0.0                         0.0   
min                           0.0                         0.0   
25%                           0.0                         0.0   
50%                           0.0                         0.0   
75%                           0.0                         0.0   
max                           0.0                         0.0   

       Special char frequency - !  Special char frequency - @  \
count                20000.000000                     20000.0   
mean                     0.689200                         0.0   
std                      1.984465                         0.0   
min                      0.000000                         0.0   
25%                      0.000000                         0.0   
50%                      0.000000                         0.0   
75%                      0.000000                         0.0   
max                     59.000000                         0.0   

       Special char frequency - #  Special char frequency - $  \
count                     20000.0                     20000.0   
mean                          0.0                         0.0   
std                           0.0                         0.0   
min                           0.0                         0.0   
25%                           0.0                         0.0   
50%                           0.0                         0.0   
75%                           0.0                         0.0   
max                           0.0                         0.0   

       Special char frequency - %  Special char frequency - ^  \
count                     20000.0                     20000.0   
mean                          0.0                         0.0   
std                           0.0                         0.0   
min                           0.0                         0.0   
25%                           0.0                         0.0   
50%                           0.0                         0.0   
75%                           0.0                         0.0   
max                           0.0                         0.0   

       Special char frequency - &  Special char frequency - *  \
count                     20000.0                     20000.0   
mean                          0.0                         0.0   
std                           0.0                         0.0   
min                           0.0                         0.0   
25%                           0.0                         0.0   
50%                           0.0                         0.0   
75%                           0.0                         0.0   
max                           0.0                         0.0   

       Special char frequency - (  Special char frequency - )  \
count                20000.000000                20000.000000   
mean                     0.806550                    0.909400   
std                      2.815639                    3.347619   
min                      0.000000                    0.000000   
25%                      0.000000                    0.000000   
50%                      0.000000                    0.000000   
75%                      1.000000                    1.000000   
max                    282.000000                  282.000000   

       Special char frequency - -  Special char frequency - _  \
count                20000.000000                     20000.0   
mean                     1.485200                         0.0   
std                      3.543234                         0.0   
min                      0.000000                         0.0   
25%                      0.000000                         0.0   
50%                      0.000000                         0.0   
75%                      2.000000   

## Values not seen by the our freq detection
https://babelstone.co.uk/Unicode/whatisit.html - use this to find special character names

In [91]:
print("…" == "...")
# … known as elipsis
# special_char_df.columns.delete(0)
# special_char_df.columns
# 
unseen_values = np.copy(test.columns)
for special_char_value in special_char_df.columns:
    for index in range(len(test.columns)):
        if test.columns[index] == special_char_value:
            unseen_values = np.delete(unseen_values, np.where(unseen_values==test.columns[index]))
unseen_values

False


array(['Common char trigram 1', 'Common char trigram 2',
       'Common char trigram 3', 'Common char trigram 4',
       'Common char trigram 5', 'Common char trigram 6',
       'Common char trigram 7', 'Common char trigram 8',
       'Common char trigram 9', 'Common char trigram 10',
       'Common char trigram 11', 'Common char trigram 12',
       'Common char trigram 13', 'Common char trigram 14',
       'Common char trigram 15', 'Common char trigram 16',
       'Common char trigram 17', 'Common char trigram 18',
       'Common char trigram 19', 'Common char trigram 20',
       'Common char trigram 21', 'Common char trigram 22',
       'Common char trigram 23', 'Common char trigram 24',
       'Common char trigram 25', 'Common char trigram 26',
       'Common char trigram 27', 'Common char trigram 28',
       'Common char trigram 29', 'Common char trigram 30',
       'Common char trigram 31', 'Common char trigram 32',
       'Common char trigram 33', 'Common char trigram 34',
      

### Lexical Features - Word (22)

#### Total # of words (1)

In [92]:
essay_word_counts = []

def check_text_file_word_len(file_path): 
    wordCount = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
        lines = data.split()
        wordCount+=len(lines)
    return wordCount

dataset_looper(essay_word_counts, check_text_file_word_len)

In [93]:
essay_word_counts

[(1, 222),
 (2, 265),
 (3, 303),
 (4, 405),
 (5, 212),
 (6, 333),
 (7, 1001),
 (8, 310),
 (9, 879),
 (10, 407),
 (11, 756),
 (12, 610),
 (13, 112),
 (14, 302),
 (15, 274),
 (16, 560),
 (17, 256),
 (18, 330),
 (19, 783),
 (20, 397),
 (21, 169),
 (22, 689),
 (23, 258),
 (24, 476),
 (25, 92),
 (26, 398),
 (27, 243),
 (28, 159),
 (29, 110),
 (30, 549),
 (31, 571),
 (32, 530),
 (33, 480),
 (34, 136),
 (35, 108),
 (36, 270),
 (37, 423),
 (38, 463),
 (39, 672),
 (40, 256),
 (41, 605),
 (42, 598),
 (43, 451),
 (44, 437),
 (45, 591),
 (46, 1171),
 (47, 453),
 (48, 336),
 (49, 199),
 (50, 444),
 (51, 460),
 (52, 246),
 (53, 827),
 (54, 157),
 (55, 97),
 (56, 201),
 (57, 238),
 (58, 136),
 (59, 457),
 (60, 258),
 (61, 309),
 (62, 269),
 (63, 355),
 (64, 234),
 (65, 344),
 (66, 385),
 (67, 883),
 (68, 480),
 (69, 177),
 (70, 314),
 (71, 335),
 (72, 512),
 (73, 461),
 (74, 468),
 (75, 412),
 (76, 298),
 (77, 351),
 (78, 480),
 (79, 302),
 (80, 310),
 (81, 461),
 (82, 332),
 (83, 529),
 (84, 416),
 

#### Average # of words per sentence (1)

In [94]:
# Defined here for the following functions
def check_essay_sentence_count(file_path): 
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    return len(sent_tokenize(data))

In [95]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks
essay_avg_words_per_sentence = []
def check_avg_words_per_sentence(file_path): 
    wordCount = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
        lines = data.split()
        wordCount+=len(lines)
    total_sentences = check_essay_sentence_count(file_path)
    avg_words_per_sentence = wordCount/total_sentences
    return avg_words_per_sentence

dataset_looper(essay_avg_words_per_sentence, check_avg_words_per_sentence)

In [96]:
essay_avg_words_per_sentence

[(1, 12.333333333333334),
 (2, 12.045454545454545),
 (3, 10.448275862068966),
 (4, 13.5),
 (5, 21.2),
 (6, 17.526315789473685),
 (7, 16.966101694915253),
 (8, 14.090909090909092),
 (9, 17.235294117647058),
 (10, 15.074074074074074),
 (11, 16.085106382978722),
 (12, 15.25),
 (13, 28.0),
 (14, 15.1),
 (15, 14.421052631578947),
 (16, 16.96969696969697),
 (17, 15.058823529411764),
 (18, 15.0),
 (19, 30.115384615384617),
 (20, 15.26923076923077),
 (21, 16.9),
 (22, 18.13157894736842),
 (23, 10.75),
 (24, 16.413793103448278),
 (25, 18.4),
 (26, 18.952380952380953),
 (27, 12.789473684210526),
 (28, 17.666666666666668),
 (29, 18.333333333333332),
 (30, 17.70967741935484),
 (31, 12.41304347826087),
 (32, 17.666666666666668),
 (33, 17.77777777777778),
 (34, 22.666666666666668),
 (35, 36.0),
 (36, 15.882352941176471),
 (37, 14.586206896551724),
 (38, 18.52),
 (39, 16.390243902439025),
 (40, 13.473684210526315),
 (41, 13.444444444444445),
 (42, 18.6875),
 (43, 18.791666666666668),
 (44, 13.2424242

#### Total # of out-of-vocabulary words (1)

In [108]:
english_vocab = set(nltk_words.words())


def count_oov_words(file_path, vocab):
    oov_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read()

    # Tokenize the text
    tokens = word_tokenize(data)

    # Count OOV words
    for token in tokens:
        if token.lower() not in vocab:
            oov_count += 1
            
    return oov_count


In [109]:
oov_counts = []

# dataset_looper(oov_counts, count_oov_words)
dataset_looper(oov_counts, lambda path: count_oov_words(path, english_vocab))

In [110]:
oov_counts

[(1, 80),
 (2, 74),
 (3, 92),
 (4, 133),
 (5, 46),
 (6, 111),
 (7, 245),
 (8, 89),
 (9, 195),
 (10, 100),
 (11, 190),
 (12, 222),
 (13, 15),
 (14, 87),
 (15, 101),
 (16, 164),
 (17, 89),
 (18, 104),
 (19, 169),
 (20, 120),
 (21, 19),
 (22, 174),
 (23, 84),
 (24, 177),
 (25, 20),
 (26, 85),
 (27, 71),
 (28, 48),
 (29, 25),
 (30, 109),
 (31, 177),
 (32, 205),
 (33, 87),
 (34, 35),
 (35, 27),
 (36, 74),
 (37, 81),
 (38, 114),
 (39, 197),
 (40, 86),
 (41, 189),
 (42, 130),
 (43, 118),
 (44, 128),
 (45, 202),
 (46, 242),
 (47, 106),
 (48, 75),
 (49, 91),
 (50, 170),
 (51, 137),
 (52, 76),
 (53, 162),
 (54, 49),
 (55, 23),
 (56, 26),
 (57, 70),
 (58, 48),
 (59, 158),
 (60, 77),
 (61, 112),
 (62, 83),
 (63, 88),
 (64, 76),
 (65, 103),
 (66, 144),
 (67, 266),
 (68, 154),
 (69, 45),
 (70, 87),
 (71, 88),
 (72, 154),
 (73, 111),
 (74, 121),
 (75, 132),
 (76, 112),
 (77, 126),
 (78, 140),
 (79, 100),
 (80, 100),
 (81, 140),
 (82, 93),
 (83, 180),
 (84, 154),
 (85, 120),
 (86, 56),
 (87, 98),
 (88

#### Average # of out-of-vocabulary words (1)

In [113]:
english_vocab = set(nltk_words.words())

def calculate_oov_average(file_path):
    oov_count = 0
    total_words = 0
    
    with open(file_path, encoding='utf-8') as file:
        data = file.read()
    
    # Tokenize the text
    tokens = word_tokenize(data)
    
    # Count OOV words and total words
    for token in tokens:
        # Count only if it's a word (ignoring punctuation)
        if token.isalpha():
            total_words += 1
            if token.lower() not in english_vocab:
                oov_count += 1
                
    # Calculate the average OOV words per total words
    average_oov = oov_count / total_words if total_words > 0 else 0
    return average_oov

In [114]:
average_oov_list = []
dataset_looper(average_oov_list, calculate_oov_average)

In [115]:
for item in average_oov_list:
    print(item)


(1, 0.1643835616438356)
(2, 0.11969111969111969)
(3, 0.10702341137123746)
(4, 0.10327455919395466)
(5, 0.10328638497652583)
(6, 0.1580547112462006)
(7, 0.09017223910840932)
(8, 0.1465798045602606)
(9, 0.112)
(10, 0.10421836228287841)
(11, 0.096)
(12, 0.1644295302013423)
(13, 0.02702702702702703)
(14, 0.15100671140939598)
(15, 0.13533834586466165)
(16, 0.10128913443830571)
(17, 0.13043478260869565)
(18, 0.12307692307692308)
(19, 0.08801020408163265)
(20, 0.11450381679389313)
(21, 0.011834319526627219)
(22, 0.08259587020648967)
(23, 0.1450980392156863)
(24, 0.16344086021505377)
(25, 0.12087912087912088)
(26, 0.07868020304568528)
(27, 0.10084033613445378)
(28, 0.10191082802547771)
(29, 0.06481481481481481)
(30, 0.08058608058608059)
(31, 0.11964285714285715)
(32, 0.22692307692307692)
(33, 0.06485355648535565)
(34, 0.08208955223880597)
(35, 0.102803738317757)
(36, 0.10902255639097744)
(37, 0.04716981132075472)
(38, 0.10964912280701754)
(39, 0.09174311926605505)
(40, 0.1388888888888889)
(41,

#### Most frequent word uni/bi/tri grams (6*3)

In [124]:
english_stopwords = set(stopwords.words('english'))

In [126]:
def check_most_freq_unigrams(file_path, stopwords_set):
    with open(file_path, encoding='utf-8') as file:
        text = file.read().lower()

    tokens = nltk.word_tokenize(text)
    # tokens = [token for token in tokens if token not in string.punctuation and token not in stopwords.words('english')]

    # Filter out punctuation and stopwords more efficiently
    filtered_tokens = [token for token in tokens if token not in string.punctuation and token not in stopwords_set]
    
    
    # Generate and count unigrams
    unigrams = Counter(filtered_tokens)
    most_common_unigrams = unigrams.most_common(6)
    
    most_common_unigrams_dict = {f'Most frequent unigrams {index + 1}': unigram[1] for index, unigram in enumerate(most_common_unigrams)}
    
    # Ensure 6 entries in the dictionary
    for index in range(len(most_common_unigrams_dict) + 1, 7):
        most_common_unigrams_dict[f'Most frequent unigrams {index}'] = 0
    
    return most_common_unigrams_dict


In [132]:
def check_most_freq_bigrams(file_path, stopwords_set):
    with open(file_path, encoding='utf-8') as file:
        text = file.read().lower()

    tokens = nltk.word_tokenize(text)
    filtered_tokens = [token for token in tokens if token not in string.punctuation and token not in stopwords_set]
    
    bigrams_list = list(ngrams(filtered_tokens, 2))
    most_common_bigrams = Counter(bigrams_list).most_common(6)
    
    most_common_bigrams_dict = {f'Most frequent bigrams {index + 1}': bigram[1] for index, bigram in enumerate(most_common_bigrams)}
    
    for index in range(len(most_common_bigrams_dict) + 1, 7):
        most_common_bigrams_dict[f'Most frequent bigrams {index}'] = 0
    
    return most_common_bigrams_dict


In [137]:
def check_most_freq_trigrams(file_path, stopwords_set):
    with open(file_path, encoding='utf-8') as file:
        text = file.read().lower()

    tokens = nltk.word_tokenize(text)
    filtered_tokens = [token for token in tokens if token not in string.punctuation and token not in stopwords_set]
    
    trigrams_list = list(ngrams(filtered_tokens, 3))
    most_common_trigrams = Counter(trigrams_list).most_common(6)
    
    most_common_trigrams_dict = {f'Most frequent trigrams {index + 1}': trigram[1] for index, trigram in enumerate(most_common_trigrams)}
    
    for index in range(len(most_common_trigrams_dict) + 1, 7):
        most_common_trigrams_dict[f'Most frequent trigrams {index}'] = 0
    
    return most_common_trigrams_dict


In [127]:
essays_most_freq_unigrams = []

# Populate the list using dataset_looper
# dataset_looper(essays_most_freq_unigrams, check_most_freq_unigrams)
dataset_looper(essays_most_freq_unigrams, lambda path: check_most_freq_unigrams(path, english_stopwords))

# Add 'Id' to each dictionary and prepare a new list
new_most_freq_unigrams = []
for item in essays_most_freq_unigrams:
    item[1]['Id'] = item[0]
    new_most_freq_unigrams.append(item[1])

# Update the original list
essays_most_freq_unigrams = new_most_freq_unigrams

In [134]:
essays_most_freq_bigrams = []

# Populate the list using dataset_looper
# dataset_looper(essays_most_freq_bigrams, check_most_freq_bigrams)
dataset_looper(essays_most_freq_bigrams, lambda path: check_most_freq_bigrams(path, english_stopwords))

# Add 'Id' to each dictionary and prepare a new list
new_most_freq_bigrams = []
for item in essays_most_freq_bigrams:
    item[1]['Id'] = item[0]
    new_most_freq_bigrams.append(item[1])

# Update the original list
essays_most_freq_bigrams = new_most_freq_bigrams

In [138]:
essays_most_freq_trigrams = []

# Populate the list using dataset_looper
# dataset_looper(essays_most_freq_trigrams, check_most_freq_trigrams)
dataset_looper(essays_most_freq_trigrams, lambda path: check_most_freq_trigrams(path, english_stopwords))

# Add 'Id' to each dictionary and prepare a new list
new_most_freq_trigrams = []
for item in essays_most_freq_trigrams:
    item[1]['Id'] = item[0]
    new_most_freq_trigrams.append(item[1])

# Update the original list
essays_most_freq_trigrams = new_most_freq_trigrams


In [128]:
pd.DataFrame(essays_most_freq_unigrams).head()

Most frequent unigrams 1  Most frequent unigrams 2  \
0                         5                         5   
1                         3                         3   
2                         7                         6   
3                         8                         7   
4                         6                         5   

   Most frequent unigrams 3  Most frequent unigrams 4  \
0                         4                         4   
1                         3                         3   
2                         5                         4   
3                         6                         6   
4                         5                         3   

   Most frequent unigrams 5  Most frequent unigrams 6  Id  
0                         3                         2   1  
1                         2                         2   2  
2                         4                         3   3  
3                         5                         4   4  
4                         3                         3   5

In [130]:
pd.DataFrame(essays_most_freq_bigrams).head()

Most frequent bigrams 1  Most frequent bigrams 2  Most frequent bigrams 3  \
0                        3                        2                        2   
1                        2                        1                        1   
2                        3                        3                        2   
3                        3                        2                        2   
4                        5                        2                        1   

   Most frequent bigrams 4  Most frequent bigrams 5  Most frequent bigrams 6  \
0                        1                        1                        1   
1                        1                        1                        1   
2                        2                        2                        1   
3                        2                        2                        1   
4                        1                        1                        1   

   Id  
0   1  
1   2  
2   3  
3   4  
4   5

In [131]:
pd.DataFrame(essays_most_freq_bigrams)

Most frequent bigrams 1  Most frequent bigrams 2  \
0                            3                        2   
1                            2                        1   
2                            3                        3   
3                            3                        2   
4                            5                        2   
...                        ...                      ...   
19995                        2                        2   
19996                        2                        1   
19997                        4                        2   
19998                        2                        1   
19999                        2                        2   

       Most frequent bigrams 3  Most frequent bigrams 4  \
0                            2                        1   
1                            1                        1   
2                            2                        2   
3                            2                        2   
4                            1                        1   
...                        ...                      ...   
19995                        1                        1   
19996                        1                        1   
19997                        2                        2   
19998                        1                        1   
19999                        1                        1   

       Most frequent bigrams 5  Most frequent bigrams 6     Id  
0                            1                        1      1  
1                            1                        1      2  
2                            2                        1      3  
3                            2                        1      4  
4                            1                        1      5  
...                        ...                      ...    ...  
19995                        1                        1  19996  
19996                        1                        1  19997  
19997                        1                        1  19998  
19998                        1                        1  19999  
19999                        1                        1  20000  

[20000 rows x 7 columns]

In [139]:
pd.DataFrame(essays_most_freq_trigrams).head()

Most frequent trigrams 1  Most frequent trigrams 2  \
0                         2                         1   
1                         1                         1   
2                         2                         2   
3                         1                         1   
4                         1                         1   

   Most frequent trigrams 3  Most frequent trigrams 4  \
0                         1                         1   
1                         1                         1   
2                         1                         1   
3                         1                         1   
4                         1                         1   

   Most frequent trigrams 5  Most frequent trigrams 6  Id  
0                         1                         1   1  
1                         1                         1   2  
2                         1                         1   3  
3                         1                         1   4  
4                         1                         1   5

In [140]:
pd.DataFrame(essays_most_freq_unigrams).shape[0]
pd.DataFrame(essays_most_freq_bigrams).shape[0]
pd.DataFrame(essays_most_freq_trigrams).shape[0]


20000

### Lexical Features - POS related (60)

#### Average # of POS types per sentence (1)

In [141]:
essays_avg_pos_types_per_sentence = []
# punctuation that nltk doesn't catch
string.punctuation = string.punctuation+"''"+"``"+":"+"--"+"..."
def check_avg_pos_types_per_sentence(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
#     data =  re.sub('[^a-zA-Z]', ' ', data)
    data = nltk.word_tokenize(data)
    words_without_punctuations = [word for word in data if word not in string.punctuation]

    pos_tags = nltk.pos_tag(words_without_punctuations)
#     pos_tags = nltk.pos_tag(data)
    list_of_pos_tags = []
    for tag in pos_tags:
        list_of_pos_tags.append(tag[1])
        
    total_sentences = check_essay_sentence_count(file_path)
    avg_pos_types_per_sentence = len(pos_tags)/total_sentences
    
    return avg_pos_types_per_sentence
#     return Counter(list_of_pos_tags)

dataset_looper(essays_avg_pos_types_per_sentence, check_avg_pos_types_per_sentence)

In [142]:
essays_avg_pos_types_per_sentence

[(1, 12.555555555555555),
 (2, 12.045454545454545),
 (3, 10.551724137931034),
 (4, 13.933333333333334),
 (5, 21.5),
 (6, 17.789473684210527),
 (7, 17.491525423728813),
 (8, 14.090909090909092),
 (9, 17.41176470588235),
 (10, 15.185185185185185),
 (11, 16.319148936170212),
 (12, 15.55),
 (13, 28.25),
 (14, 15.2),
 (15, 14.473684210526315),
 (16, 17.060606060606062),
 (17, 15.588235294117647),
 (18, 15.454545454545455),
 (19, 30.73076923076923),
 (20, 15.5),
 (21, 17.2),
 (22, 18.473684210526315),
 (23, 10.875),
 (24, 16.79310344827586),
 (25, 18.6),
 (26, 19.428571428571427),
 (27, 13.210526315789474),
 (28, 18.22222222222222),
 (29, 18.666666666666668),
 (30, 17.903225806451612),
 (31, 12.565217391304348),
 (32, 17.7),
 (33, 18.37037037037037),
 (34, 23.666666666666668),
 (35, 38.0),
 (36, 16.058823529411764),
 (37, 15.068965517241379),
 (38, 18.64),
 (39, 16.585365853658537),
 (40, 13.842105263157896),
 (41, 13.755555555555556),
 (42, 19.15625),
 (43, 19.125),
 (44, 13.242424242424242

#### POS Type to unique words ratio (1)

TODO | Currently there is a small problem where words such as "Brian's" are split by the nltk.word_tokenize() function. These splits are counted as unique words and I am wondering if we should care about these edge cases? Seem annoying to catch, but interested to see how often a problem like this occurs.

In [143]:
essays_pos_type_to_unique_words_ratio = []
def check_pos_type_to_unique_words(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    data = nltk.word_tokenize(data)
    words_without_punctuations = [word for word in data if word not in string.punctuation]
    total_unique_words = len(set(words_without_punctuations))
    
    pos_tags = nltk.pos_tag(words_without_punctuations)
#     pos_tags = nltk.pos_tag(data)
    list_of_pos_tags = []
    for tag in pos_tags:
        list_of_pos_tags.append(tag[1])
    
    avg_pos_type_to_unique_words_ratio = len(pos_tags)/total_unique_words
    
    return avg_pos_type_to_unique_words_ratio
#     data =  re.sub('[^a-zA-Z]', ' ', data)
    
dataset_looper(essays_pos_type_to_unique_words_ratio, check_pos_type_to_unique_words)

In [144]:
essays_pos_type_to_unique_words_ratio

[(1, 1.5066666666666666),
 (2, 1.6358024691358024),
 (3, 1.8106508875739644),
 (4, 1.908675799086758),
 (5, 1.6666666666666667),
 (6, 1.715736040609137),
 (7, 2.6805194805194805),
 (8, 1.8452380952380953),
 (9, 2.49438202247191),
 (10, 1.8894009216589862),
 (11, 2.4272151898734178),
 (12, 2.1084745762711865),
 (13, 1.5694444444444444),
 (14, 1.7572254335260116),
 (15, 1.5625),
 (16, 2.1165413533834587),
 (17, 1.6878980891719746),
 (18, 1.8681318681318682),
 (19, 2.654485049833887),
 (20, 1.848623853211009),
 (21, 1.72),
 (22, 2.1144578313253013),
 (23, 1.6730769230769231),
 (24, 1.6735395189003437),
 (25, 1.2916666666666667),
 (26, 1.9805825242718447),
 (27, 1.7552447552447552),
 (28, 1.561904761904762),
 (29, 1.4933333333333334),
 (30, 2.423580786026201),
 (31, 2.181132075471698),
 (32, 2.107142857142857),
 (33, 1.9604743083003953),
 (34, 1.5434782608695652),
 (35, 1.6056338028169015),
 (36, 1.70625),
 (37, 2.111111111111111),
 (38, 1.7718631178707225),
 (39, 2.214983713355049),
 (40,

#### Total # of stopwords (1)

In [145]:
stop_words = stopwords.words('english')
essays_total_stop_words = []

def check_total_stop_words(file_path): 
    stop_words_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    word_tokens = word_tokenize(data)
    for word in word_tokens:
        if word in stop_words:
            stop_words_count+=1
    return stop_words_count
#         lines = data.split()
#         wordCount+=len(lines)
#     return wordCount

dataset_looper(essays_total_stop_words, check_total_stop_words)
# nltk.download('stopwords')
# print(stopwords.words('english'))

In [146]:
essays_total_stop_words

[(1, 104),
 (2, 133),
 (3, 158),
 (4, 199),
 (5, 103),
 (6, 160),
 (7, 526),
 (8, 168),
 (9, 435),
 (10, 205),
 (11, 381),
 (12, 296),
 (13, 65),
 (14, 138),
 (15, 120),
 (16, 290),
 (17, 117),
 (18, 162),
 (19, 441),
 (20, 215),
 (21, 101),
 (22, 351),
 (23, 117),
 (24, 206),
 (25, 43),
 (26, 192),
 (27, 127),
 (28, 75),
 (29, 59),
 (30, 315),
 (31, 284),
 (32, 232),
 (33, 243),
 (34, 65),
 (35, 56),
 (36, 132),
 (37, 234),
 (38, 215),
 (39, 345),
 (40, 121),
 (41, 301),
 (42, 327),
 (43, 241),
 (44, 212),
 (45, 281),
 (46, 635),
 (47, 236),
 (48, 185),
 (49, 104),
 (50, 221),
 (51, 199),
 (52, 125),
 (53, 432),
 (54, 73),
 (55, 43),
 (56, 116),
 (57, 124),
 (58, 67),
 (59, 230),
 (60, 118),
 (61, 148),
 (62, 134),
 (63, 167),
 (64, 122),
 (65, 184),
 (66, 176),
 (67, 410),
 (68, 245),
 (69, 80),
 (70, 165),
 (71, 178),
 (72, 255),
 (73, 232),
 (74, 233),
 (75, 210),
 (76, 134),
 (77, 165),
 (78, 248),
 (79, 162),
 (80, 151),
 (81, 221),
 (82, 159),
 (83, 263),
 (84, 189),
 (85, 148),

#### Average # of stopwords per sentence (1)

In [147]:
stop_words = stopwords.words('english')
essays_avg_stopwords_per_sentence = []

def check_avg_stopwords_per_sentence(file_path): 
    stop_words_count = 0
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    word_tokens = word_tokenize(data)
    
    for word in word_tokens:
        if word in stop_words:
            stop_words_count+=1
    total_sentences = check_essay_sentence_count(file_path)
    avg_words_per_sentence = stop_words_count/total_sentences
    return avg_words_per_sentence

dataset_looper(essays_avg_stopwords_per_sentence, check_avg_stopwords_per_sentence)

In [148]:
essays_avg_stopwords_per_sentence

[(1, 5.777777777777778),
 (2, 6.045454545454546),
 (3, 5.448275862068965),
 (4, 6.633333333333334),
 (5, 10.3),
 (6, 8.421052631578947),
 (7, 8.915254237288135),
 (8, 7.636363636363637),
 (9, 8.529411764705882),
 (10, 7.592592592592593),
 (11, 8.106382978723405),
 (12, 7.4),
 (13, 16.25),
 (14, 6.9),
 (15, 6.315789473684211),
 (16, 8.787878787878787),
 (17, 6.882352941176471),
 (18, 7.363636363636363),
 (19, 16.96153846153846),
 (20, 8.26923076923077),
 (21, 10.1),
 (22, 9.236842105263158),
 (23, 4.875),
 (24, 7.103448275862069),
 (25, 8.6),
 (26, 9.142857142857142),
 (27, 6.684210526315789),
 (28, 8.333333333333334),
 (29, 9.833333333333334),
 (30, 10.161290322580646),
 (31, 6.173913043478261),
 (32, 7.733333333333333),
 (33, 9.0),
 (34, 10.833333333333334),
 (35, 18.666666666666668),
 (36, 7.764705882352941),
 (37, 8.068965517241379),
 (38, 8.6),
 (39, 8.414634146341463),
 (40, 6.368421052631579),
 (41, 6.688888888888889),
 (42, 10.21875),
 (43, 10.041666666666666),
 (44, 6.424242424

#### Most frequent POS unigrams (32)

In [149]:
essays_most_freq_pos_unigram = []
def check_most_freq_pos_unigram(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    data = nltk.word_tokenize(data)
    words_without_punctuations = [word for word in data if word not in string.punctuation]

    pos_tags = nltk.pos_tag(words_without_punctuations)
    list_of_pos_tags = []
    for tag in pos_tags:
        list_of_pos_tags.append(tag[1])
        
    most_common_pos_unigram = Counter(list_of_pos_tags).most_common(32)
    
    index = 1
    most_common_pos_unigram_dict = {}
    for unigram in most_common_pos_unigram:
        most_common_pos_unigram_dict[f'Most frequent POS unigrams {index}'] = unigram[1]
        index+=1
        
    pos_unigram_dict_len = len(most_common_pos_unigram_dict)
    max_unigrams_count = 32
    if pos_unigram_dict_len < max_unigrams_count:
        for index in range(pos_unigram_dict_len, max_unigrams_count + 1):
            most_common_pos_unigram_dict[f'Most frequent POS unigrams {index}'] = 0
    
    return most_common_pos_unigram_dict

dataset_looper(essays_most_freq_pos_unigram, check_most_freq_pos_unigram)


new_most_freq_pos_unigrams = []
for item in essays_most_freq_pos_unigram:
    item[1]['Id'] = item[0] 
    new_most_freq_pos_unigrams.append(item[1])

essays_most_freq_pos_unigram = new_most_freq_pos_unigrams

In [150]:
pd.DataFrame(essays_most_freq_pos_unigram)

Most frequent POS unigrams 1  Most frequent POS unigrams 2  \
0                                29                            25   
1                                36                            26   
2                                39                            33   
3                                56                            45   
4                                41                            28   
...                             ...                           ...   
19995                            34                            24   
19996                            20                            19   
19997                            40                            31   
19998                            13                             7   
19999                            13                            13   

       Most frequent POS unigrams 3  Most frequent POS unigrams 4  \
0                                25                            21   
1                                25                            22   
2                                29                            28   
3                                33                            33   
4                                22                            17   
...                             ...                           ...   
19995                            22                            19   
19996                            15                            13   
19997                            30                            21   
19998                             7                             4   
19999                            13                             8   

       Most frequent POS unigrams 5  Most frequent POS unigrams 6  \
0                                17                            17   
1                                21                            20   
2                                26                            24   
3                                30                            29   
4                                14                            13   
...                             ...                           ...   
19995                            14                            13   
19996                            12                            12   
19997                            19                            18   
19998                             4                             4   
19999                             8                             7   

       Most frequent POS unigrams 7  Most frequent POS unigrams 8  \
0                                16                            15   
1                                19                            16   
2                                22                            19   
3                                29                            28   
4                                12                            10   
...                             ...                           ...   
19995                            12                            11   
19996                            12                            10   
19997                            17                            11   
19998                             4                             4   
19999                             7                             6   

       Most frequent POS unigrams 9  Most frequent POS unigrams 10  \
0                                14                              9   
1                                12                             11   
2                                18                             10   
3                                28                             16   
4                                10                              8   
...                             ...                            ...   
19995                            11                              8   
19996                            10                              7   
19997                            10                          

#### Most frequent POS bigrams (16)

In [151]:
essays_most_freq_pos_bigrams = []
def check_most_freq_pos_bigrams(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    data = nltk.word_tokenize(data)
    words_without_punctuations = [word for word in data if word not in string.punctuation]
    
    pos_tags = nltk.pos_tag(words_without_punctuations)
    list_of_pos_tags = []
    for tag in pos_tags:
        list_of_pos_tags.append(tag[1])
        
    bigrams_list = list(ngrams(list_of_pos_tags, 2))
    most_common_pos_bigrams = Counter(bigrams_list).most_common(16)
    
    index = 1
    most_common_pos_bigrams_dict = {}
    for unigram in most_common_pos_bigrams:
        most_common_pos_bigrams_dict[f'Most frequent POS bigrams {index}'] = unigram[1]
        index+=1
    return most_common_pos_bigrams_dict

dataset_looper(essays_most_freq_pos_bigrams, check_most_freq_pos_bigrams)

new_most_freq_pos_bigrams = []
for item in essays_most_freq_pos_bigrams:
    item[1]['Id'] = item[0] 
    new_most_freq_pos_bigrams.append(item[1])
    
essays_most_freq_pos_bigrams = new_most_freq_pos_bigrams

In [152]:
# contains 0 null values | there are 16 common POS bigram tags
pd.DataFrame(essays_most_freq_pos_bigrams)

Most frequent POS bigrams 1  Most frequent POS bigrams 2  \
0                               11                            8   
1                               10                            9   
2                               13                           12   
3                               15                           13   
4                               15                           11   
...                            ...                          ...   
19995                            9                            8   
19996                            6                            6   
19997                           13                           12   
19998                            4                            4   
19999                            6                            4   

       Most frequent POS bigrams 3  Most frequent POS bigrams 4  \
0                                7                          6.0   
1                                8                          7.0   
2                               12                          9.0   
3                               13                         12.0   
4                               10                          6.0   
...                            ...                          ...   
19995                            7                          6.0   
19996                            5                          5.0   
19997                           10                         10.0   
19998                            3                          3.0   
19999                            4                          4.0   

       Most frequent POS bigrams 5  Most frequent POS bigrams 6  \
0                              6.0                          5.0   
1                              7.0                          6.0   
2                              8.0                          7.0   
3                             12.0                         10.0   
4                              6.0                          5.0   
...                            ...                          ...   
19995                          6.0                          6.0   
19996                          4.0                          4.0   
19997                         10.0                          8.0   
19998                          2.0                          2.0   
19999                          4.0                          3.0   

       Most frequent POS bigrams 7  Most frequent POS bigrams 8  \
0                              5.0                          5.0   
1                              6.0                          5.0   
2                              6.0                          6.0   
3                             10.0                          9.0   
4                              5.0                          5.0   
...                            ...                          ...   
19995                          6.0                          6.0   
19996                          4.0                          4.0   
19997                          8.0                          6.0   
19998                          2.0                          2.0   
19999                          3.0                          3.0   

       Most frequent POS bigrams 9  Most frequent POS bigrams 10  \
0                              5.0                           5.0   
1                              5.0                           5.0   
2                              6.0                           6.0   
3                              9.0                           9.0   
4                              4.0                           4.0   
...                            ...                           ...   
19995                          6.0                           6.0   
19996                          4.0                           3.0   
19997                          6.0                           6.0   
19998                          2.0                           2.0   
19999                          3.0     

#### Most frequent POS trigrams

In [153]:
essays_most_freq_pos_trigrams = []
def check_most_freq_pos_trigrams(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read().lower()
    data = nltk.word_tokenize(data)
    words_without_punctuations = [word for word in data if word not in string.punctuation]
    
    pos_tags = nltk.pos_tag(words_without_punctuations)
    list_of_pos_tags = []
    for tag in pos_tags:
        list_of_pos_tags.append(tag[1])
        
    trigrams_list = list(ngrams(list_of_pos_tags, 3))
    most_common_pos_trigrams = Counter(trigrams_list).most_common(8)
    
    index = 1
    most_common_pos_trigrams_dict = {}
    for unigram in most_common_pos_trigrams:
        most_common_pos_trigrams_dict[f'Most frequent POS trigrams {index}'] = unigram[1]
        index+=1
    return most_common_pos_trigrams_dict

dataset_looper(essays_most_freq_pos_trigrams, check_most_freq_pos_trigrams)

new_most_freq_pos_trigrams = []
for item in essays_most_freq_pos_trigrams:
    item[1]['Id'] = item[0] 
    new_most_freq_pos_trigrams.append(item[1])
    
essays_most_freq_pos_trigrams = new_most_freq_pos_trigrams

In [154]:
pd.DataFrame(essays_most_freq_pos_trigrams)

Most frequent POS trigrams 1  Most frequent POS trigrams 2  \
0                                 6                             5   
1                                 5                             4   
2                                 6                             5   
3                                 7                             7   
4                                 7                             7   
...                             ...                           ...   
19995                             5                             4   
19996                             3                             3   
19997                             6                             6   
19998                             2                             2   
19999                             2                             2   

       Most frequent POS trigrams 3  Most frequent POS trigrams 4  \
0                                 4                           3.0   
1                                 4                           4.0   
2                                 5                           4.0   
3                                 7                           4.0   
4                                 3                           2.0   
...                             ...                           ...   
19995                             3                           3.0   
19996                             2                           2.0   
19997                             5                           4.0   
19998                             2                           2.0   
19999                             2                           2.0   

       Most frequent POS trigrams 5  Most frequent POS trigrams 6  \
0                               3.0                           3.0   
1                               3.0                           3.0   
2                               4.0                           4.0   
3                               4.0                           3.0   
4                               2.0                           2.0   
...                             ...                           ...   
19995                           3.0                           3.0   
19996                           2.0                           2.0   
19997                           4.0                           3.0   
19998                           2.0                           2.0   
19999                           2.0                           2.0   

       Most frequent POS trigrams 7  Most frequent POS trigrams 8     Id  
0                               3.0                           3.0      1  
1                               3.0                           3.0      2  
2                               4.0                           4.0      3  
3                               3.0                           3.0      4  
4                               2.0                           2.0      5  
...                             ...                           ...    ...  
19995                           3.0                           3.0  19996  
19996                           2.0                           2.0  19997  
19997                           3.0                           3.0  19998  
19998                           1.0                           1.0  19999  
19999                           1.0                           1.0  20000  

[20000 rows x 9 columns]

### Lexical Features - Sentence level

#### \# of sentences (1)

In [155]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks

essay_sentence_count = []
def check_essay_sentence_count(file_path): 
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    return len(sent_tokenize(data))

dataset_looper(essay_sentence_count, check_essay_sentence_count)

In [156]:
essay_sentence_count

[(1, 18),
 (2, 22),
 (3, 29),
 (4, 30),
 (5, 10),
 (6, 19),
 (7, 59),
 (8, 22),
 (9, 51),
 (10, 27),
 (11, 47),
 (12, 40),
 (13, 4),
 (14, 20),
 (15, 19),
 (16, 33),
 (17, 17),
 (18, 22),
 (19, 26),
 (20, 26),
 (21, 10),
 (22, 38),
 (23, 24),
 (24, 29),
 (25, 5),
 (26, 21),
 (27, 19),
 (28, 9),
 (29, 6),
 (30, 31),
 (31, 46),
 (32, 30),
 (33, 27),
 (34, 6),
 (35, 3),
 (36, 17),
 (37, 29),
 (38, 25),
 (39, 41),
 (40, 19),
 (41, 45),
 (42, 32),
 (43, 24),
 (44, 33),
 (45, 33),
 (46, 62),
 (47, 23),
 (48, 21),
 (49, 24),
 (50, 29),
 (51, 30),
 (52, 10),
 (53, 39),
 (54, 12),
 (55, 5),
 (56, 11),
 (57, 14),
 (58, 7),
 (59, 35),
 (60, 21),
 (61, 23),
 (62, 15),
 (63, 11),
 (64, 17),
 (65, 19),
 (66, 22),
 (67, 56),
 (68, 36),
 (69, 12),
 (70, 19),
 (71, 19),
 (72, 33),
 (73, 22),
 (74, 28),
 (75, 21),
 (76, 16),
 (77, 28),
 (78, 34),
 (79, 21),
 (80, 21),
 (81, 25),
 (82, 16),
 (83, 40),
 (84, 32),
 (85, 22),
 (86, 12),
 (87, 19),
 (88, 69),
 (89, 5),
 (90, 21),
 (91, 105),
 (92, 32),
 (93,

#### Average length of sentences (1)

In [157]:
# https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/?ref=ml_lbp
# Code utilized from geeksforgeeks

essay_avg_sentence_length = []
def check_avg_sentence_length(file_path): 
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    sentences = sent_tokenize(data)
    sentences_total = len(sentences)
    sentence_length_total = 0
    for sentence in sentences:
        sentence_length_total+=len(sentence)
    avg_sentence_length = sentence_length_total/sentences_total
    return avg_sentence_length

dataset_looper(essay_avg_sentence_length, check_avg_sentence_length)

In [158]:
essay_avg_sentence_length

[(1, 67.83333333333333),
 (2, 61.04545454545455),
 (3, 55.172413793103445),
 (4, 74.66666666666667),
 (5, 123.1),
 (6, 99.10526315789474),
 (7, 94.89830508474576),
 (8, 74.22727272727273),
 (9, 95.23529411764706),
 (10, 83.29629629629629),
 (11, 91.2127659574468),
 (12, 86.025),
 (13, 150.5),
 (14, 86.35),
 (15, 86.47368421052632),
 (16, 90.57575757575758),
 (17, 86.88235294117646),
 (18, 85.81818181818181),
 (19, 166.96153846153845),
 (20, 82.6923076923077),
 (21, 95.1),
 (22, 100.28947368421052),
 (23, 59.916666666666664),
 (24, 98.24137931034483),
 (25, 109.0),
 (26, 107.0952380952381),
 (27, 69.10526315789474),
 (28, 96.77777777777777),
 (29, 101.66666666666667),
 (30, 94.48387096774194),
 (31, 65.45652173913044),
 (32, 106.36666666666666),
 (33, 98.11111111111111),
 (34, 125.5),
 (35, 194.33333333333334),
 (36, 94.17647058823529),
 (37, 76.48275862068965),
 (38, 104.8),
 (39, 90.53658536585365),
 (40, 77.89473684210526),
 (41, 74.26666666666667),
 (42, 95.46875),
 (43, 102.9166666

#### Flesch Kincaid

In [164]:
essay_flesch_kincaid_scores = []

def check_flesch_kincaid(file_path):
    with open(file_path, encoding='utf-8') as file:
        data = file.read()  
    r = Readability(data)
    # Calculate and store Flesch Grade Level Ease
    return r.flesch_kincaid().score

dataset_looper(essay_flesch_kincaid_scores, check_flesch_kincaid)

NameError: name 'Readability' is not defined

In [160]:
essay_flesch_kincaid_scores

[]

## Combining Features into a dataframe

In [165]:
# Labels - entity types
labels_df = pd.DataFrame(essays_labels)

# Lexical Features - Character Based (112) - decreased from 120 to 112 due to paper having incorrect feature amount
total_char_counts_df = pd.DataFrame(essay_total_char_counts, columns=['Id', 'Total characters'])
percentage_of_digits_df = pd.DataFrame(essays_digit_percentage, columns=['Id', 'Digit percentage'])
percentage_of_letters_df = pd.DataFrame(essays_letter_percentage, columns=['Id', 'Letter percentage'])
percentage_of_uppercase_letters_df = pd.DataFrame(uppercase_percentage, columns=['Id', 'Uppercase percentage'])
total_sentence_count_df = pd.DataFrame(essay_sentence_count, columns=['Id', 'Total number of sentences'])
frequency_char_unigram_df = pd.DataFrame(essays_char_frequency)
most_common_char_bigrams_df = pd.DataFrame(essays_char_bigrams)
most_common_char_trigrams_df = pd.DataFrame(essays_char_trigrams)

# Lexical Features - Digits, special characters, punctuation chars (36) - decreased from 40 to 36 due to paper having incorrect feature amount
frequency_of_digits_df = pd.DataFrame(essays_digit_frequency)
frequency_of_special_chars_df = pd.DataFrame(essays_char_frequency)

# Lexical Features - Word (22)
total_word_count_df = pd.DataFrame(essay_word_counts, columns=['Id', 'Total words'])
average_words_per_sentence_df = pd.DataFrame(essay_avg_words_per_sentence, columns=['Id', 'Average words per sentence'])
total_oov_words_df = pd.DataFrame(oov_counts, columns=['Id', 'Total OOV words'])
average_oov_words_df = pd.DataFrame(average_oov_list, columns=['Id', 'Average OOV words'])
essays_most_freq_unigrams_df = pd.DataFrame(essays_most_freq_unigrams)
essays_most_freq_bigrams_df = pd.DataFrame(essays_most_freq_bigrams)
essays_most_freq_trigrams_df = pd.DataFrame(essays_most_freq_trigrams)

# Lexical Features - POS related (60)

average_pos_types_per_sentence_df = pd.DataFrame(essays_avg_pos_types_per_sentence, columns=['Id', 'Average POS types per sentence'])
pos_to_unique_words_ratio_df = pd.DataFrame(essays_pos_type_to_unique_words_ratio, columns=['Id', 'POS to unique words ratio'])
total_stopwords_df = pd.DataFrame(essays_total_stop_words, columns=['Id', 'Total stopwords'])
average_stopwords_per_sentence_df = pd.DataFrame(essays_avg_stopwords_per_sentence, columns=['Id', 'Average stopwords per sentence'])
most_frequent_pos_unigrams_df =  pd.DataFrame(essays_most_freq_pos_unigram)
most_frequent_pos_bigrams_df = pd.DataFrame(essays_most_freq_pos_bigrams)
most_frequent_pos_trigrams_df = pd.DataFrame(essays_most_freq_pos_trigrams)

# Lexical Features - Sentence level (2)
total_sentences_df = pd.DataFrame(essay_sentence_count, columns=['Id', 'Total sentences'])
average_sentence_length_df = pd.DataFrame(essay_avg_sentence_length, columns=['Id', 'Average sentence length'])

# Flesch-kincaid
flesch_kincaid_df = pd.DataFrame(essay_flesch_kincaid_scores, columns=['Id', 'Flesch-kincaid grade level score'])

In [58]:
data_frames = [
    # Labels - entity types
    labels_df,
    
    # Lexical Features - Character Based (112)
    total_char_counts_df,
    percentage_of_digits_df,
    percentage_of_letters_df,
    percentage_of_uppercase_letters_df,
    total_sentence_count_df,
    frequency_char_unigram_df,
    most_common_char_bigrams_df,
    most_common_char_trigrams_df,

    # Lexical Features - Digits, special characters, punctuation chars (36)
    frequency_of_digits_df,
    frequency_of_special_chars_df,

    # Lexical Features - Word (22
    total_word_count_df,
    average_words_per_sentence_df,
    total_oov_words_df,
    average_oov_words_df,
    essays_most_freq_unigrams_df,
    essays_most_freq_bigrams_df,
    essays_most_freq_trigrams_df,

    # Lexical Features - POS related (60)
    average_pos_types_per_sentence_df,
    pos_to_unique_words_ratio_df,
    total_stopwords_df,
    average_stopwords_per_sentence_df,
    most_frequent_pos_unigrams_df,
    most_frequent_pos_bigrams_df,
    most_frequent_pos_trigrams_df,
    
    
    # Lexical Features - Sentence level (2)
    total_sentences_df,
    average_sentence_length_df
    
    # Flesch-kincaid
    flesch_kincaid_df
]

In [166]:
data_frames = [
    # Lexical Features - Word (22)
    total_word_count_df,
    average_words_per_sentence_df,
    total_oov_words_df,
    average_oov_words_df,
    essays_most_freq_unigrams_df,
    essays_most_freq_bigrams_df,
    essays_most_freq_trigrams_df,
    
]

In [168]:
total_word_count_df
for df in data_frames:
    print(df.shape)
    
for df in data_frames:
    print(df.columns)


(20000, 2)
(20000, 2)
(20000, 2)
(20000, 2)
(20000, 7)
(20000, 7)
(20000, 7)
Index(['Id', 'Total words'], dtype='object')
Index(['Id', 'Average words per sentence'], dtype='object')
Index(['Id', 'Total OOV words'], dtype='object')
Index(['Id', 'Average OOV words'], dtype='object')
Index(['Most frequent unigrams 1', 'Most frequent unigrams 2',
       'Most frequent unigrams 3', 'Most frequent unigrams 4',
       'Most frequent unigrams 5', 'Most frequent unigrams 6', 'Id'],
      dtype='object')
Index(['Most frequent bigrams 1', 'Most frequent bigrams 2',
       'Most frequent bigrams 3', 'Most frequent bigrams 4',
       'Most frequent bigrams 5', 'Most frequent bigrams 6', 'Id'],
      dtype='object')
Index(['Most frequent trigrams 1', 'Most frequent trigrams 2',
       'Most frequent trigrams 3', 'Most frequent trigrams 4',
       'Most frequent trigrams 5', 'Most frequent trigrams 6', 'Id'],
      dtype='object')


In [59]:
# from functools import reduce
# # extracted_features = pd.DataFrame(essay_sentence_count, columns=['Id', 'Total number of sentences'])
# # extracted_features.merge(total_char_counts_df, on='Id')
# # extracted_features

# df_merged = reduce(lambda  left,right: pd.merge(left,right,on=['Id']), data_frames)
# os.chdir(r"C:\Users\user\Desktop\UHManoaClasses\ICS499\ChatGPT-Generated-Text-Detection") 
# df_merged.to_csv("text-features - BDD.csv", index=False,)

In [173]:
# Create df_merged
df_merged = reduce(lambda  left,right: pd.merge(left,right,on=['Id']), data_frames)

In [174]:
df_merged

Id  Total words  Average words per sentence  Total OOV words  \
0          1          222                   12.333333               80   
1          2          265                   12.045455               74   
2          3          303                   10.448276               92   
3          4          405                   13.500000              133   
4          5          212                   21.200000               46   
...      ...          ...                         ...              ...   
19995  19996          203                   22.555556               37   
19996  19997          157                   19.625000               31   
19997  19998          249                   24.900000               51   
19998  19999           65                   21.666667               16   
19999  20000          105                   26.250000               22   

       Average OOV words  Most frequent unigrams 1  Most frequent unigrams 2  \
0               0.164384                         5                         5   
1               0.119691                         3                         3   
2               0.107023                         7                         6   
3               0.103275                         8                         7   
4               0.103286                         6                         5   
...                  ...                       ...                       ...   
19995           0.059406                         4                         3   
19996           0.096154                         5                         3   
19997           0.096774                         5                         4   
19998           0.123077                         3                         2   
19999           0.096154                         3                         3   

       Most frequent unigrams 3  Most frequent unigrams 4  \
0                             4                         4   
1                             3                         3   
2                             5                         4   
3                             6                         6   
4                             5                         3   
...                         ...                       ...   
19995                         3                         2   
19996                         2                         2   
19997                         3                         3   
19998                         2                         2   
19999                         2                         2   

       Most frequent unigrams 5  Most frequent unigrams 6  \
0                             3                         2   
1                             2                         2   
2                             4                         3   
3                             5                         4   
4                             3                         3   
...                         ...                       ...   
19995                         2                         2   
19996                         2                         2   
19997                         3                         2   
19998                         1                         1   
19999                         2                         2   

       Most frequent bigrams 1  Most frequent bigrams 2  \
0                            3                        2   
1                            2                        1   
2                            3                        3   
3                            3                        2   
4                            5                        2   
...                        ...                      ...   
19995                        2                        2   
19996                        2                        1   
19997                        4                        2   
19998                        2                        1   
19999                        2               

In [172]:
# Export to csv in current directory
os.getcwd()

# directory: '/Users/hoobot/VS Code/ChatGPT-Generated-Text-Detection'
os.chdir('/Users/hoobot/VS Code/ChatGPT-Generated-Text-Detection')
df_merged.to_csv('additional-features-new-dataset.csv', index=False)

## Merge into already existing csv

Total words_x  Average words per sentence_x  Total OOV words  \
Id                                                                  
1              277                     27.700000               65   
2              318                     22.714286               65   
3              402                     23.647059              105   
4              305                     21.785714               73   
5              421                     24.764706               85   
..             ...                           ...              ...   
248            275                     15.277778               57   
249            481                     32.066667               71   
250            538                     20.692308              120   
251            187                     15.583333               34   
252            378                     14.538462               87   

     Average OOV words  Most frequent unigrams 1  Most frequent unigrams 2  \
Id                                                                           
1             0.145455                         6                         5   
2             0.107595                        12                        12   
3             0.142500                        11                        11   
4             0.092105                         9                         9   
5             0.109785                        14                        12   
..                 ...                       ...                       ...   
248           0.063433                         5                         4   
249           0.068750                         9                         6   
250           0.119403                         9                         7   
251           0.064171                         4                         4   
252           0.064000                         9                         8   

     Most frequent unigrams 3  Most frequent unigrams 4  \
Id                                                        
1                           5                         5   
2                           6                         5   
3                           9                         6   
4                           9                         8   
5                           9                         8   
..                        ...                       ...   
248                         4                         4   
249                         6                         6   
250                         5                         5   
251                         4                         4   
252                         5                         5   

     Most frequent unigrams 5  Most frequent unigrams 6  \
Id                                                        
1                           5                         4   
2                           5                         5   
3                           5                         5   
4                           7                         5   
5                           7                         5   
..                        ...                       ...   
248                         3                         3   
249                         5                         3   
250                         5                         4   
251                         3                         3   
252                         5                         4   

     Most frequent bigrams 1  Most frequent bigrams 2  \
Id                                                      
1                          4                        3   
2                         12                        4   
3                          5                        4   
4                          9                        8   
5                         12                        7   
..                       ...                      ...   
248                        2                        2   
249                        2               

In [63]:
merged_csv = pd.read_csv('merged-text-features.csv').set_index('Id')
merged_csv = merged_csv.join(flesch_kincaid_df.set_index('Id'), on='Id')
os.chdir(r"C:\Users\user\Desktop\UHManoaClasses\ICS499\ChatGPT-Generated-Text-Detection") 
merged_csv = merged_csv.reset_index()
merged_csv.to_csv("merged-text-features.csv", index=False)

ValueError: columns overlap but no suffix specified: Index(['Flesch-kincaid grade level score'], dtype='object')